In [1]:
# 1. Create a function that takes in three arguments;
# Wikipedia data, Kaggle metadata, and MovieLens rating data (from Kaggle)

import json
import pandas as pd
import numpy as np

import re

from sqlalchemy import create_engine
import psycopg2

from config import db_password

import time



In [2]:
def clean_movie(movie):
    movie = dict(movie) #create a non-destructive copy
    return movie

# 1. Add the clean movie function that takes in the argument, "movie".
def clean_movie(movie):
    movie = dict(movie) #create a non-destructive copy
    alt_titles = {}
    # combine alternate titles into one list
    for key in ['Also known as','Arabic','Cantonese','Chinese','French',
                'Hangul','Hebrew','Hepburn','Japanese','Literally',
                'Mandarin','McCune-Reischauer','Original title','Polish',
                'Revised Romanization','Romanized','Russian',
                'Simplified','Traditional','Yiddish']:
        if key in movie:
            alt_titles[key] = movie[key]
            movie.pop(key)
    if len(alt_titles) > 0:
        movie['alt_titles'] = alt_titles

    # merge column names
    def change_column_name(old_name, new_name):
        if old_name in movie:
            movie[new_name] = movie.pop(old_name)
    change_column_name('Adaptation by', 'Writer(s)')
    change_column_name('Country of origin', 'Country')
    change_column_name('Directed by', 'Director')
    change_column_name('Distributed by', 'Distributor')
    change_column_name('Edited by', 'Editor(s)')
    change_column_name('Length', 'Running time')
    change_column_name('Original release', 'Release date')
    change_column_name('Music by', 'Composer(s)')
    change_column_name('Produced by', 'Producer(s)')
    change_column_name('Producer', 'Producer(s)')
    change_column_name('Productioncompanies ', 'Production company(s)')
    change_column_name('Productioncompany ', 'Production company(s)')
    change_column_name('Released', 'Release Date')
    change_column_name('Release Date', 'Release date')
    change_column_name('Screen story by', 'Writer(s)')
    change_column_name('Screenplay by', 'Writer(s)')
    change_column_name('Story by', 'Writer(s)')
    change_column_name('Theme music composer', 'Composer(s)')
    change_column_name('Written by', 'Writer(s)')

    return movie

In [3]:
# 17. Create the path to your file directory and variables for the three files.
file_dir = 'Data'
# The Wikipedia data
wiki_file = f'{file_dir}/wikipedia-movies.json'
# The Kaggle metadata
kaggle_file = f'{file_dir}/movies_metadata.csv'
# The MovieLens rating data.
ratings_file = f'{file_dir}/ratings.csv'

In [4]:
print(wiki_file)

Data/wikipedia-movies.json


In [5]:
# Read in the kaggle metadata and MovieLens ratings CSV files as Pandas DataFrames.
kaggle_metadata = pd.read_csv(kaggle_file, low_memory=False)
ratings = pd.read_csv(ratings_file)

In [6]:
print(kaggle_metadata)

       adult                              belongs_to_collection    budget  \
0      False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
1      False                                                NaN  65000000   
2      False  {'id': 119050, 'name': 'Grumpy Old Men Collect...         0   
3      False                                                NaN  16000000   
4      False  {'id': 96871, 'name': 'Father of the Bride Col...         0   
...      ...                                                ...       ...   
45461  False                                                NaN         0   
45462  False                                                NaN         0   
45463  False                                                NaN         0   
45464  False                                                NaN         0   
45465  False                                                NaN         0   

                                                  genres  \
0      [{'id': 

In [7]:
pd.read_json(wiki_file)

url    year  \
0     https://en.wikipedia.org/wiki/The_Adventures_o...  1990.0   
1     https://en.wikipedia.org/wiki/After_Dark,_My_S...  1990.0   
2      https://en.wikipedia.org/wiki/Air_America_(film)  1990.0   
3       https://en.wikipedia.org/wiki/Alice_(1990_film)  1990.0   
4         https://en.wikipedia.org/wiki/Almost_an_Angel  1990.0   
...                                                 ...     ...   
7306    https://en.wikipedia.org/wiki/Holmes_%26_Watson  2018.0   
7307     https://en.wikipedia.org/wiki/Vice_(2018_film)  2018.0   
7308  https://en.wikipedia.org/wiki/On_the_Basis_of_Sex  2018.0   
7309  https://en.wikipedia.org/wiki/Destroyer_(2018_...  2018.0   
7310  https://en.wikipedia.org/wiki/Black_Mirror:_Ba...  2018.0   

                                  imdb_link                            title  \
0     https://www.imdb.com/title/tt0098987/  The Adventures of Ford Fairlane   
1     https://www.imdb.com/title/tt0098994/             After Dark, My Sweet   
2     https://www.imdb.com/title/tt0099005/                      Air America   
3     https://www.imdb.com/title/tt0099012/                            Alice   
4     https://www.imdb.com/title/tt0099018/                  Almost an Angel   
...                                     ...                              ...   
7306  https://www.imdb.com/title/tt1255919/                  Holmes & Watson   
7307  https://www.imdb.com/title/tt6266538/                             Vice   
7308  https://www.imdb.com/title/tt4669788/              On the Basis of Sex   
7309  https://www.imdb.com/title/tt7137380/                        Destroyer   
7310  https://www.imdb.com/title/tt9495224/                     Bandersnatch   

             Directed by                                        Produced by  \
0           Renny Harlin                         [Steve Perry, Joel Silver]   
1            James Foley                        [Ric Kidney, Robert Redlin]   
2     Roger Spottiswoode                                     Daniel Melnick   
3            Woody Allen                                    Robert Greenhut   
4           John Cornell                                       John Cornell   
...                  ...                                                ...   
7306          Etan Cohen  [Will Ferrell, Adam McKay, Jimmy Miller, Clayt...   
7307          Adam McKay  [Brad Pitt, Dede Gardner, Jeremy Kleiner, Kevi...   
7308          Mimi Leder                                     Robert W. Cort   
7309        Karyn Kusama             [Fred Berger, Phil Hay, Matt Manfredi]   
7310         David Slade                                     Russell McLean   

                                   Screenplay by                     Story by  \
0     [David Arnott, James Cappe, Daniel Waters]  [David Arnott, James Cappe]   
1                   [James Foley, Robert Redlin]                          NaN   
2                     [John Eskow, Richard Rush]                          NaN   
3                                            NaN                          NaN   
4                                            NaN                          NaN   
...                                          ...                          ...   
7306                                  Etan Cohen                          NaN   
7307                                         NaN                          NaN   
7308                                         NaN                          NaN   
7309                                         NaN                          NaN   
7310                                         NaN                          NaN   

                                               Based on  \
0                           [Characters, by Rex Weiner]   
1     [the novel, After Dark, My Sweet, by, Jim Thom...   
2                [Air America, by, Christopher Robbins]   
3                                                   NaN   
4                                                   NaN   
...       

In [8]:

# Open the read the Wikipedia data JSON file.
with open(wiki_file, mode="r") as file:
    wiki_movies_raw = json.load(file)


In [9]:
for movie in wiki_movies_raw:
   print(movie)

{'url': 'https://en.wikipedia.org/wiki/The_Adventures_of_Ford_Fairlane', 'year': 1990, 'imdb_link': 'https://www.imdb.com/title/tt0098987/', 'title': 'The Adventures of Ford Fairlane', 'Directed by': 'Renny Harlin', 'Produced by': ['Steve Perry', 'Joel Silver'], 'Screenplay by': ['David Arnott', 'James Cappe', 'Daniel Waters'], 'Story by': ['David Arnott', 'James Cappe'], 'Based on': ['Characters', 'by Rex Weiner'], 'Starring': ['Andrew Dice Clay', 'Wayne Newton', 'Priscilla Presley', 'Lauren Holly', 'Morris Day', 'Robert Englund', "Ed O'Neill"], 'Narrated by': 'Andrew "Dice" Clay', 'Music by': ['Cliff Eidelman', 'Yello'], 'Cinematography': 'Oliver Wood', 'Edited by': 'Michael Tronick', 'Productioncompany ': 'Silver Pictures', 'Distributed by': '20th Century Fox', 'Release date': ['July 11, 1990', '(', '1990-07-11', ')'], 'Running time': '102 minutes', 'Country': 'United States', 'Language': 'English', 'Budget': '$20 million', 'Box office': '$21.4 million'}
{'url': 'https://en.wikipedi

{'url': 'https://en.wikipedia.org/wiki/Sense_and_Sensibility_(film)', 'year': 1995, 'imdb_link': 'https://www.imdb.com/title/tt0114388/', 'title': 'Sense and Sensibility', 'Directed by': 'Ang Lee', 'Produced by': 'Lindsay Doran', 'Screenplay by': 'Emma Thompson', 'Based on': ['Sense and Sensibility', 'by', 'Jane Austen'], 'Starring': ['Emma Thompson', 'Alan Rickman', 'Kate Winslet', 'Hugh Grant'], 'Music by': 'Patrick Doyle', 'Cinematography': 'Michael Coulter', 'Edited by': 'Tim Squyres', 'Productioncompany ': ['Columbia Pictures', 'Mirage Enterprises'], 'Distributed by': 'Sony Pictures Releasing', 'Release date': ['December 13, 1995', '(', '1995-12-13', ')', '(United States)'], 'Running time': '136 minutes', 'Country': 'United States', 'Language': 'English', 'Budget': '$16 million', 'Box office': '$135 million'}
{'url': 'https://en.wikipedia.org/wiki/Seven_(1995_film)', 'year': 1995, 'imdb_link': 'https://www.imdb.com/title/tt0114369/', 'title': 'Seven', 'Directed by': 'David Fincher

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [10]:
# 3. Write a list comprehension to filter out TV shows.
wiki_movies =[movie for movie in wiki_movies_raw
              if ('Director ' in movie or 'Directed by' in movie)
              and 'imdb_link' in movie
              and 'No. of episodes' not in movie]


In [11]:
for movie in wiki_movies_raw:
   print(movie)

{'url': 'https://en.wikipedia.org/wiki/The_Adventures_of_Ford_Fairlane', 'year': 1990, 'imdb_link': 'https://www.imdb.com/title/tt0098987/', 'title': 'The Adventures of Ford Fairlane', 'Directed by': 'Renny Harlin', 'Produced by': ['Steve Perry', 'Joel Silver'], 'Screenplay by': ['David Arnott', 'James Cappe', 'Daniel Waters'], 'Story by': ['David Arnott', 'James Cappe'], 'Based on': ['Characters', 'by Rex Weiner'], 'Starring': ['Andrew Dice Clay', 'Wayne Newton', 'Priscilla Presley', 'Lauren Holly', 'Morris Day', 'Robert Englund', "Ed O'Neill"], 'Narrated by': 'Andrew "Dice" Clay', 'Music by': ['Cliff Eidelman', 'Yello'], 'Cinematography': 'Oliver Wood', 'Edited by': 'Michael Tronick', 'Productioncompany ': 'Silver Pictures', 'Distributed by': '20th Century Fox', 'Release date': ['July 11, 1990', '(', '1990-07-11', ')'], 'Running time': '102 minutes', 'Country': 'United States', 'Language': 'English', 'Budget': '$20 million', 'Box office': '$21.4 million'}
{'url': 'https://en.wikipedi

{'url': 'https://en.wikipedia.org/wiki/I_Love_You_to_Death', 'year': 1990, 'imdb_link': 'https://www.imdb.com/title/tt0099819/', 'title': 'I Love You to Death', 'Directed by': 'Lawrence Kasdan', 'Produced by': 'Jeffrey Lurie', 'Written by': 'John Kostmayer', 'Starring': ['Kevin Kline', 'Tracey Ullman', 'William Hurt', 'River Phoenix', 'Joan Plowright', 'Keanu Reeves'], 'Music by': 'James Horner', 'Cinematography': 'Owen Roizman', 'Edited by': 'Anne V. Coates', 'Distributed by': 'TriStar Pictures', 'Release date': ['April 6, 1990', '(', '1990-04-06', ')'], 'Running time': '97 minutes', 'Country': 'United States', 'Language': ['English', 'Italian', 'Serbo-Croatian'], 'Box office': '$16.2 million'}
{'url': 'https://en.wikipedia.org/wiki/I%27m_Dangerous_Tonight', 'year': 1990, 'imdb_link': 'https://www.imdb.com/title/tt0099822/', 'title': "I'm Dangerous Tonight", 'Based on': ["I'm Dangerous Tonight", 'by', 'Cornell Woolrich'], 'Written by': ['Bruce Lansbury', 'Philip John Taylor'], 'Direct

{'url': 'https://en.wikipedia.org/wiki/The_Face_(1996_film)', 'year': 1996, 'imdb_link': 'https://www.imdb.com/title/tt0116265/', 'title': 'A Face to Die For', 'Genre': 'Drama', 'Based on': ['The Face', 'by Marvin and Mark Werlin'], 'Written by': 'Duane Poole', 'Directed by': 'Jack Bender', 'Starring': ['Yasmine Bleeth', 'James Wilder', 'Robin Givens', 'Chandra West'], 'Music by': 'Christopher Franke', 'Country of origin': 'United States', 'Original language(s)': 'English', 'Executive producer(s)': ['Frank Konigsberg', 'Robert Levinson'], 'Producer(s)': ['Jayne Bieber', 'Duane Poole', '(co-producer0', 'Mark Werlin', '(co-producer)', 'Marvin Werlin', '(co-producer)'], 'Production location(s)': ['4th Street Viaduct, Los Angeles, California', 'Santa Fe Avenue, Downtown, Los Angeles'], 'Cinematography': 'Eagle Egilsson', 'Editor(s)': 'Mark Melnick', 'Running time': '90 minutes', 'Production company(s)': 'Konigsberg Company', 'Distributor': 'NBC', 'Original network': 'NBC', 'Picture format'

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [12]:
def extract_transform_load(kaggle_file):
     kaggle_metadata = pd.read_csv(kaggle_file, low_memory = False)
     ratings = pd.read_csv(ratings_file)
     return kaggle_metadata

In [13]:
#then call the funciton
extract_transform_load(kaggle_file)

adult                              belongs_to_collection    budget  \
0      False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
1      False                                                NaN  65000000   
2      False  {'id': 119050, 'name': 'Grumpy Old Men Collect...         0   
3      False                                                NaN  16000000   
4      False  {'id': 96871, 'name': 'Father of the Bride Col...         0   
...      ...                                                ...       ...   
45461  False                                                NaN         0   
45462  False                                                NaN         0   
45463  False                                                NaN         0   
45464  False                                                NaN         0   
45465  False                                                NaN         0   

                                                  genres  \
0      [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
1      [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...   
2      [{'id': 10749, 'name': 'Romance'}, {'id': 35, ...   
3      [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...   
4                         [{'id': 35, 'name': 'Comedy'}]   
...                                                  ...   
45461  [{'id': 18, 'name': 'Drama'}, {'id': 10751, 'n...   
45462                      [{'id': 18, 'name': 'Drama'}]   
45463  [{'id': 28, 'name': 'Action'}, {'id': 18, 'nam...   
45464                                                 []   
45465                                                 []   

                                   homepage      id    imdb_id  \
0      http://toystory.disney.com/toy-story     862  tt0114709   
1                                       NaN    8844  tt0113497   
2                                       NaN   15602  tt0113228   
3                                       NaN   31357  tt0114885   
4                                       NaN   11862  tt0113041   
...                                     ...     ...        ...   
45461  http://www.imdb.com/title/tt6209470/  439050  tt6209470   
45462                                   NaN  111109  tt2028550   
45463                                   NaN   67758  tt0303758   
45464                                   NaN  227506  tt0008536   
45465                                   NaN  461257  tt6980792   

      original_language               original_title  \
0                    en                    Toy Story   
1                    en                      Jumanji   
2                    en             Grumpier Old Men   
3                    en            Waiting to Exhale   
4                    en  Father of the Bride Part II   
...                 ...                          ...   
45461                fa                      رگ خواب   
45462                tl          Siglo ng Pagluluwal   
45463                en                     Betrayal   
45464                en          Satana likuyushchiy   
45465                en                     Queerama   

                                                overview  ... release_date  \
0      Led by Woody, Andy's toys live happily in his ...  ...   1995-10-30   
1      When siblings Judy and Peter discover an encha...  ...   1995-12-15   
2      A family wedding reignites the ancient feud be...  ...   1995-12-22   
3      Cheated on, mistreated and stepped on, the wom...  ...   1995-12-22   
4      Just when George Banks has recovered from his ...  ...   1995-02-10   
...                                                  ...  ...          ...   
45461        Rising and falling between a man and woman.  ...          NaN   
45462  An artist struggles to finish his work while a...  ...   2011-11-17   
45463  When one of her hits goes wrong, a professiona...  ...   2003-08-01   
45464  In a small town live two brothers, one a minis...  ...   1917-10-21   
45465  50 years after decriminalisati

In [14]:
for movie in wiki_movies_raw:
   print(movie)

{'url': 'https://en.wikipedia.org/wiki/The_Adventures_of_Ford_Fairlane', 'year': 1990, 'imdb_link': 'https://www.imdb.com/title/tt0098987/', 'title': 'The Adventures of Ford Fairlane', 'Directed by': 'Renny Harlin', 'Produced by': ['Steve Perry', 'Joel Silver'], 'Screenplay by': ['David Arnott', 'James Cappe', 'Daniel Waters'], 'Story by': ['David Arnott', 'James Cappe'], 'Based on': ['Characters', 'by Rex Weiner'], 'Starring': ['Andrew Dice Clay', 'Wayne Newton', 'Priscilla Presley', 'Lauren Holly', 'Morris Day', 'Robert Englund', "Ed O'Neill"], 'Narrated by': 'Andrew "Dice" Clay', 'Music by': ['Cliff Eidelman', 'Yello'], 'Cinematography': 'Oliver Wood', 'Edited by': 'Michael Tronick', 'Productioncompany ': 'Silver Pictures', 'Distributed by': '20th Century Fox', 'Release date': ['July 11, 1990', '(', '1990-07-11', ')'], 'Running time': '102 minutes', 'Country': 'United States', 'Language': 'English', 'Budget': '$20 million', 'Box office': '$21.4 million'}
{'url': 'https://en.wikipedi

{'url': 'https://en.wikipedia.org/wiki/The_Rock_(film)', 'year': 1996, 'imdb_link': 'https://www.imdb.com/title/tt0117500/', 'title': 'The Rock', 'Directed by': 'Michael Bay', 'Produced by': ['Don Simpson', 'Jerry Bruckheimer'], 'Screenplay by': ['David Weisberg', 'Douglas S. Cook', 'Mark Rosner'], 'Story by': ['David Weisberg', 'Douglas S. Cook'], 'Starring': ['Sean Connery', 'Nicolas Cage', 'Ed Harris', 'Michael Biehn', 'William Forsythe'], 'Music by': ['Nick Glennie-Smith', 'Hans Zimmer', '[1]', '[2]'], 'Cinematography': 'John Schwartzman', 'Edited by': 'Richard Francis-Bruce', 'Productioncompanies ': ['Hollywood Pictures', 'Simpson', '/', 'Bruckheimer'], 'Distributed by': 'Buena Vista Pictures', 'Release date': ['June 7, 1996', '(', '1996-06-07', ')'], 'Running time': '136 minutes', 'Country': 'United States', 'Language': 'English', 'Budget': '$75 million', 'Box office': '$335.1 million'}
{'url': 'https://en.wikipedia.org/wiki/Romeo_%2B_Juliet', 'year': 1996, 'imdb_link': 'https://

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [15]:
# 4. Write a list comprehension to iterate through the cleaned wiki movies list
# and call the clean_movie function on each movie.
clean_movies = [clean_movie(movie) for movie in wiki_movies]


In [16]:
for movie in clean_movies:
   print(movie)

{'url': 'https://en.wikipedia.org/wiki/The_Adventures_of_Ford_Fairlane', 'year': 1990, 'imdb_link': 'https://www.imdb.com/title/tt0098987/', 'title': 'The Adventures of Ford Fairlane', 'Based on': ['Characters', 'by Rex Weiner'], 'Starring': ['Andrew Dice Clay', 'Wayne Newton', 'Priscilla Presley', 'Lauren Holly', 'Morris Day', 'Robert Englund', "Ed O'Neill"], 'Narrated by': 'Andrew "Dice" Clay', 'Cinematography': 'Oliver Wood', 'Release date': ['July 11, 1990', '(', '1990-07-11', ')'], 'Running time': '102 minutes', 'Country': 'United States', 'Language': 'English', 'Budget': '$20 million', 'Box office': '$21.4 million', 'Director': 'Renny Harlin', 'Distributor': '20th Century Fox', 'Editor(s)': 'Michael Tronick', 'Composer(s)': ['Cliff Eidelman', 'Yello'], 'Producer(s)': ['Steve Perry', 'Joel Silver'], 'Production company(s)': 'Silver Pictures', 'Writer(s)': ['David Arnott', 'James Cappe']}
{'url': 'https://en.wikipedia.org/wiki/After_Dark,_My_Sweet', 'year': 1990, 'imdb_link': 'http

{'url': 'https://en.wikipedia.org/wiki/Basquiat_(film)', 'year': 1996, 'imdb_link': 'https://www.imdb.com/title/tt0115632/', 'title': 'Basquiat', 'Starring': ['Jeffrey Wright', 'David Bowie', 'Dennis Hopper', 'Gary Oldman', 'Benicio del Toro', 'Claire Forlani', 'Michael Wincott'], 'Cinematography': 'Ron Fortunato', 'Release date': ['August 9, 1996', '(', '1996-08-09', ')'], 'Running time': '106 minutes', 'Country': 'United States', 'Language': ['English', 'Spanish'], 'Budget': '$3.3 million', 'Box office': '$3 million', 'Director': 'Julian Schnabel', 'Distributor': 'Miramax Films', 'Editor(s)': 'Michael Berenbaum', 'Composer(s)': ['John Cale', 'Julian Schnabel'], 'Producer(s)': ['Joseph Allen', 'Peter Brant'], 'Writer(s)': ['John Bowe', 'Michael Holman', 'Lech Majewski']}
{'url': 'https://en.wikipedia.org/wiki/Bastard_Out_of_Carolina_(film)', 'year': 1996, 'imdb_link': 'https://www.imdb.com/title/tt0115633/', 'title': 'Bastard Out of Carolina', 'Based on': ['Bastard Out of Carolina', '

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [17]:
# 5. Read in the cleaned movies list from Step 4 as a DataFrame.
#clean_movies_df = pd.DataFrame(clean_movies)
clean_movies = [clean_movie(movie) for movie in wiki_movies]
wiki_movies_df = pd.DataFrame(clean_movies)
sorted(wiki_movies_df.columns.tolist())

['Animation by',
 'Audio format',
 'Based on',
 'Box office',
 'Budget',
 'Cinematography',
 'Color process',
 'Composer(s)',
 'Country',
 'Created by',
 'Director',
 'Distributor',
 'Editor(s)',
 'Executive producer(s)',
 'Followed by',
 'Genre',
 'Language',
 'McCune–Reischauer',
 'Narrated by',
 'Original language(s)',
 'Original network',
 'Picture format',
 'Preceded by',
 'Producer(s)',
 'Production company(s)',
 'Production location(s)',
 'Release date',
 'Running time',
 'Starring',
 'Suggested by',
 'Voices of',
 'Writer(s)',
 'alt_titles',
 'imdb_link',
 'title',
 'url',
 'year']

In [18]:
print(wiki_movies_df)

                                                    url  year  \
0     https://en.wikipedia.org/wiki/The_Adventures_o...  1990   
1     https://en.wikipedia.org/wiki/After_Dark,_My_S...  1990   
2      https://en.wikipedia.org/wiki/Air_America_(film)  1990   
3       https://en.wikipedia.org/wiki/Alice_(1990_film)  1990   
4         https://en.wikipedia.org/wiki/Almost_an_Angel  1990   
...                                                 ...   ...   
7069    https://en.wikipedia.org/wiki/Holmes_%26_Watson  2018   
7070     https://en.wikipedia.org/wiki/Vice_(2018_film)  2018   
7071  https://en.wikipedia.org/wiki/On_the_Basis_of_Sex  2018   
7072  https://en.wikipedia.org/wiki/Destroyer_(2018_...  2018   
7073  https://en.wikipedia.org/wiki/Black_Mirror:_Ba...  2018   

                                  imdb_link                            title  \
0     https://www.imdb.com/title/tt0098987/  The Adventures of Ford Fairlane   
1     https://www.imdb.com/title/tt0098994/             Aft

In [19]:
clean_movies = [clean_movie(movie) for movie in wiki_movies]
wiki_movies_df = pd.DataFrame(clean_movies)
sorted(wiki_movies_df.columns.tolist())

['Animation by',
 'Audio format',
 'Based on',
 'Box office',
 'Budget',
 'Cinematography',
 'Color process',
 'Composer(s)',
 'Country',
 'Created by',
 'Director',
 'Distributor',
 'Editor(s)',
 'Executive producer(s)',
 'Followed by',
 'Genre',
 'Language',
 'McCune–Reischauer',
 'Narrated by',
 'Original language(s)',
 'Original network',
 'Picture format',
 'Preceded by',
 'Producer(s)',
 'Production company(s)',
 'Production location(s)',
 'Release date',
 'Running time',
 'Starring',
 'Suggested by',
 'Voices of',
 'Writer(s)',
 'alt_titles',
 'imdb_link',
 'title',
 'url',
 'year']

In [20]:
  try:
      wiki_movies_df['imdb_id'] = wiki_movies_df['imdb_link'].str.extract(r'(tt\d{7})')
      wiki_movies_df.drop_duplicates(subset='imdb_id', inplace=True)
  except KeyError:
      print("A KeyError exists")

In [21]:
print(wiki_movies_df['imdb_id'])

0       tt0098987
1       tt0098994
2       tt0099005
3       tt0099012
4       tt0099018
          ...    
7069    tt1255919
7070    tt6266538
7071    tt4669788
7072    tt7137380
7073    tt9495224
Name: imdb_id, Length: 7031, dtype: object


In [22]:
#  7. Write a list comprehension to keep the columns that don't have null values from the wiki_movies_df DataFrame.
[[column,wiki_movies_df[column].isnull().sum()] for column in wiki_movies_df.columns]

[['url', 0],
 ['year', 0],
 ['imdb_link', 0],
 ['title', 1],
 ['Based on', 4850],
 ['Starring', 182],
 ['Narrated by', 6750],
 ['Cinematography', 689],
 ['Release date', 32],
 ['Running time', 139],
 ['Country', 234],
 ['Language', 242],
 ['Budget', 2293],
 ['Box office', 1546],
 ['Director', 0],
 ['Distributor', 355],
 ['Editor(s)', 546],
 ['Composer(s)', 516],
 ['Producer(s)', 202],
 ['Production company(s)', 1676],
 ['Writer(s)', 197],
 ['Genre', 6923],
 ['Original language(s)', 6873],
 ['Original network', 6906],
 ['Executive producer(s)', 6934],
 ['Production location(s)', 6984],
 ['Picture format', 6967],
 ['Audio format', 6970],
 ['Voices of', 7029],
 ['Followed by', 7022],
 ['Created by', 7021],
 ['Preceded by', 7021],
 ['Suggested by', 7030],
 ['alt_titles', 7010],
 ['Animation by', 7029],
 ['Color process', 7030],
 ['McCune–Reischauer', 7029],
 ['imdb_id', 0]]

In [23]:
[column for column in wiki_movies_df.columns if wiki_movies_df[column].isnull().sum() < len(wiki_movies_df) * 0.9]


['url',
 'year',
 'imdb_link',
 'title',
 'Based on',
 'Starring',
 'Cinematography',
 'Release date',
 'Running time',
 'Country',
 'Language',
 'Budget',
 'Box office',
 'Director',
 'Distributor',
 'Editor(s)',
 'Composer(s)',
 'Producer(s)',
 'Production company(s)',
 'Writer(s)',
 'imdb_id']

In [24]:
wiki_columns_to_keep = [column for column in wiki_movies_df.columns if wiki_movies_df[column].isnull().sum() < len(wiki_movies_df) * 0.9]
wiki_movies_df = wiki_movies_df[wiki_columns_to_keep]

In [25]:
wiki_movies_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7031 entries, 0 to 7073
Data columns (total 21 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   url                    7031 non-null   object
 1   year                   7031 non-null   int64 
 2   imdb_link              7031 non-null   object
 3   title                  7030 non-null   object
 4   Based on               2181 non-null   object
 5   Starring               6849 non-null   object
 6   Cinematography         6342 non-null   object
 7   Release date           6999 non-null   object
 8   Running time           6892 non-null   object
 9   Country                6797 non-null   object
 10  Language               6789 non-null   object
 11  Budget                 4738 non-null   object
 12  Box office             5485 non-null   object
 13  Director               7031 non-null   object
 14  Distributor            6676 non-null   object
 15  Editor(s)            

In [26]:
box_office = wiki_movies_df['Box office'].dropna()

In [27]:
def is_not_a_string(x):
    return type(x) != str
    box_office[box_office.map(is_not_a_string)]
    box_office = box_office.apply(lambda x: ' '.join(x) if type(x) == list else x)


In [28]:
box_office

0          $21.4 million
1           $2.7 million
2            $57,718,089
3             $7,331,647
4       $6,939,946 (USA)
              ...       
7068       $19.4 million
7069       $41.9 million
7070       $76.1 million
7071       $38.4 million
7072        $5.5 million
Name: Box office, Length: 5485, dtype: object

In [29]:
form_one = r'\$\d+\.?\d*\s*[mb]illion'
form_one

'\\$\\d+\\.?\\d*\\s*[mb]illion'

In [30]:
form_two = r'\$\d{1,3}(?:,\d{3})+'
box_office.str.extract(f'({form_one}|{form_two})')

0
0     $21.4 million
1      $2.7 million
2       $57,718,089
3        $7,331,647
4        $6,939,946
...             ...
7068  $19.4 million
7069  $41.9 million
7070  $76.1 million
7071  $38.4 million
7072   $5.5 million

[5485 rows x 1 columns]

In [31]:
def parse_dollars(s):
    # if s is not a string, return NaN
    if type(s) != str:
        return np.nan

    # if input is of the form $###.# million
    if re.match(r'\$\s*\d+\.?\d*\s*milli?on', s, flags=re.IGNORECASE):

        # remove dollar sign and " million"
        s = re.sub('\$|\s|[a-zA-Z]','', s)

        # convert to float and multiply by a million
        value = float(s) * 10**6

        # return value
        return value

    # if input is of the form $###.# billion
    elif re.match(r'\$\s*\d+\.?\d*\s*billi?on', s, flags=re.IGNORECASE):

        # remove dollar sign and " billion"
        s = re.sub('\$|\s|[a-zA-Z]','', s)

        # convert to float and multiply by a billion
        value = float(s) * 10**9

        # return value
        return value

    # if input is of the form $###,###,###
    elif re.match(r'\$\s*\d{1,3}(?:[,\.]\d{3})+(?!\s[mb]illion)', s, flags=re.IGNORECASE):

        # remove dollar sign and commas
        s = re.sub('\$|,','', s)

        # convert to float
        value = float(s)

        # return value
        return value

    # otherwise, return NaN
    else:
        return np.nan

In [32]:
wiki_movies_df['box_office'] = box_office.str.extract(f'({form_one}|{form_two})', flags=re.IGNORECASE)[0].apply(parse_dollars)
wiki_movies_df['box_office']

0       21400000.0
1        2700000.0
2       57718089.0
3        7331647.0
4        6939946.0
           ...    
7069    41900000.0
7070    76100000.0
7071    38400000.0
7072     5500000.0
7073           NaN
Name: box_office, Length: 7031, dtype: float64

In [33]:
budget = wiki_movies_df['Budget'].dropna()
budget = budget.map(lambda x: ' '.join(x) if type(x) == list else x)
budget = budget.str.replace(r'\$.*[-—–](?![a-z])', '$', regex=True)
matches_form_one = budget.str.contains(form_one, flags=re.IGNORECASE)
matches_form_two = budget.str.contains(form_two, flags=re.IGNORECASE)
budget = budget.str.replace(r'\[\d+\]\s*', '')
budget[~matches_form_one & ~matches_form_two]
wiki_movies_df['budget'] = budget.str.extract(f'({form_one}|{form_two})', flags=re.IGNORECASE)[0].apply(parse_dollars)
wiki_movies_df['budget']

0       20000000.0
1        6000000.0
2       35000000.0
3       12000000.0
4       25000000.0
           ...    
7069    42000000.0
7070    60000000.0
7071    20000000.0
7072     9000000.0
7073           NaN
Name: budget, Length: 7031, dtype: float64

In [34]:
release_date = wiki_movies_df['Release date'].dropna().apply(lambda x: ' '.join(x) if type(x) == list else x)
date_form_one = r'(?:January|February|March|April|May|June|July|August|September|October|November|December)\s[123]\d,\s\d{4}'
date_form_two = r'\d{4}.[01]\d.[123]\d'
date_form_three = r'(?:January|February|March|April|May|June|July|August|September|October|November|December)\s\d{4}'
date_form_four = r'\d{4}'
release_date.str.extract(f'({date_form_one}|{date_form_two}|{date_form_three}|{date_form_four})', flags=re.IGNORECASE)
wiki_movies_df['release_date'] = pd.to_datetime(release_date.str.extract(f'({date_form_one}|{date_form_two}|{date_form_three}|{date_form_four})')[0], infer_datetime_format=True)
wiki_movies_df['release_date']

0      1990-07-11
1      1990-05-17
2      1990-08-10
3      1990-12-25
4      1990-12-19
          ...    
7069   2018-12-25
7070   2018-12-11
7071   2018-01-01
7072   2018-08-31
7073   2018-12-01
Name: release_date, Length: 7031, dtype: datetime64[ns]

In [35]:
running_time = wiki_movies_df['Running time'].dropna().apply(lambda x: ' '.join(x) if type(x) == list else x)
running_time[running_time.str.contains(r'^\d*\s*minutes$', flags=re.IGNORECASE) != True]
running_time[running_time.str.contains(r'^\d*\s*m', flags=re.IGNORECASE) != True]
running_time_extract = running_time.str.extract(r'(\d+)\s*ho?u?r?s?\s*(\d*)|(\d+)\s*m')
running_time_extract = running_time_extract.apply(lambda col: pd.to_numeric(col, errors='coerce')).fillna(0)
wiki_movies_df['running_time'] = running_time_extract.apply(lambda row: row[0]*60 + row[1] if row[2] == 0 else row[2], axis=1)
wiki_movies_df['running_time'] 

0       102.0
1       114.0
2       113.0
3       106.0
4        95.0
        ...  
7069     90.0
7070    132.0
7071    120.0
7072    123.0
7073     90.0
Name: running_time, Length: 7031, dtype: float64

In [36]:
def extract_transform_load():
    # Read in the kaggle metadata and MovieLens ratings CSV files as Pandas DataFrames.
    kaggle_metadata = pd.read_csv(kaggle_file, low_memory = False)
    ratings = pd.read_csv(ratings_file)

    # Open the read the Wikipedia data JSON file.
    with open(wiki_file, mode="r") as file:
        wiki_movies_raw = json.load(file)
        
    # 3. Write a list comprehension to filter out TV shows.
    wiki_movies =[movie for movie in wiki_movies_raw
                  if ('Director ' in movie or 'Directed by' in movie)
                  and 'imdb_link' in movie
                  and 'No. of episodes' not in movie]

    # 4. Write a list comprehension to iterate through the cleaned wiki movies list
    # and call the clean_movie function on each movie.
    clean_movies = [clean_movie(movie) for movie in wiki_movies]

    # 5. Read in the cleaned movies list from Step 4 as a DataFrame.
    clean_movies = [clean_movie(movie) for movie in wiki_movies]
    wiki_movies_df = pd.DataFrame(clean_movies)
    sorted(wiki_movies_df.columns.tolist())
    
    # 6. Write a try-except block to catch errors while extracting the IMDb ID using a regular expression string and
    #  dropping any imdb_id duplicates. If there is an error, capture and print the exception.
    try:
        wiki_movies_df['imdb_id'] = wiki_movies_df['imdb_link'].str.extract(r'(tt\d{7})')
        wiki_movies_df.drop_duplicates(subset='imdb_id', inplace=True)
    except KeyError:
        print("A KeyError exists")
      #  7. Write a list comprehension to keep the columns that don't have null values from the wiki_movies_df DataFrame.
    
    wiki_columns_to_keep = [column for column in wiki_movies_df.columns if wiki_movies_df[column].isnull().sum() < len(wiki_movies_df) * 0.9]
    wiki_movies_df = wiki_movies_df[wiki_columns_to_keep]
    
    # 8. Create a variable that will hold the non-null values from the “Box office” column.
    box_office = wiki_movies_df['Box office'].dropna()
    
    # 9. Convert the box office data created in Step 8 to string values using the lambda and join functions.
    def is_not_a_string(x):
        return type(x) != str
    box_office[box_office.map(is_not_a_string)]
    box_office = box_office.apply(lambda x: ' '.join(x) if type(x) == list else x)
    

    # 10. Write a regular expression to match the six elements of "form_one" of the box office data.
    form_one = r'\$\d+\.?\d*\s*[mb]illion'

    # 11. Write a regular expression to match the three elements of "form_two" of the box office data.
    
    form_two = r'\$\d{1,3}(?:,\d{3})+'

    # 12. Add the parse_dollars function.
    
    def parse_dollars(s):
    # if s is not a string, return NaN
        if type(s) != str:
            return np.nan

    # if input is of the form $###.# million
        if re.match(r'\$\s*\d+\.?\d*\s*milli?on', s, flags=re.IGNORECASE):

            # remove dollar sign and " million"
            s = re.sub('\$|\s|[a-zA-Z]','', s)

            # convert to float and multiply by a million
            value = float(s) * 10**6

            # return value
            return value

        # if input is of the form $###.# billion
        elif re.match(r'\$\s*\d+\.?\d*\s*billi?on', s, flags=re.IGNORECASE):

            # remove dollar sign and " billion"
            s = re.sub('\$|\s|[a-zA-Z]','', s)

            # convert to float and multiply by a billion
            value = float(s) * 10**9

            # return value
            return value

        # if input is of the form $###,###,###
        elif re.match(r'\$\s*\d{1,3}(?:[,\.]\d{3})+(?!\s[mb]illion)', s, flags=re.IGNORECASE):

            # remove dollar sign and commas
            s = re.sub('\$|,','', s)

            # convert to float
            value = float(s)

            # return value
            return value

        # otherwise, return NaN
        else:
            return np.nan

    # 13. Clean the box office column in the wiki_movies_df DataFrame.

        wiki_movies_df['box_office'] = box_office.str.extract(f'({form_one}|{form_two})', flags=re.IGNORECASE)[0].apply(parse_dollars)

    # 14. Clean the budget column in the wiki_movies_df DataFrame.
        budget = wiki_movies_df['Budget'].dropna()
        budget = budget.map(lambda x: ' '.join(x) if type(x) == list else x)
        budget = budget.str.replace(r'\$.*[-—–](?![a-z])', '$', regex=True)
        matches_form_one = budget.str.contains(form_one, flags=re.IGNORECASE)
        matches_form_two = budget.str.contains(form_two, flags=re.IGNORECASE)
        budget = budget.str.replace(r'\[\d+\]\s*', '')
        budget[~matches_form_one & ~matches_form_two]
        wiki_movies_df['budget'] = budget.str.extract(f'({form_one}|{form_two})', flags=re.IGNORECASE)[0].apply(parse_dollars)


    # 15. Clean the release date column in the wiki_movies_df DataFrame.
        release_date = wiki_movies_df['Release date'].dropna().apply(lambda x: ' '.join(x) if type(x) == list else x)
        date_form_one = r'(?:January|February|March|April|May|June|July|August|September|October|November|December)\s[123]\d,\s\d{4}'
        date_form_two = r'\d{4}.[01]\d.[123]\d'
        date_form_three = r'(?:January|February|March|April|May|June|July|August|September|October|November|December)\s\d{4}'
        date_form_four = r'\d{4}'
        release_date.str.extract(f'({date_form_one}|{date_form_two}|{date_form_three}|{date_form_four})', flags=re.IGNORECASE)
        wiki_movies_df['release_date'] = pd.to_datetime(release_date.str.extract(f'({date_form_one}|{date_form_two}|{date_form_three}|{date_form_four})')[0], infer_datetime_format=True)

    # 16. Clean the running time column in the wiki_movies_df DataFrame.
        running_time = wiki_movies_df['Running time'].dropna().apply(lambda x: ' '.join(x) if type(x) == list else x)
        running_time[running_time.str.contains(r'^\d*\s*minutes$', flags=re.IGNORECASE) != True]
        running_time[running_time.str.contains(r'^\d*\s*m', flags=re.IGNORECASE) != True]
        running_time_extract = running_time.str.extract(r'(\d+)\s*ho?u?r?s?\s*(\d*)|(\d+)\s*m')
        running_time_extract = running_time_extract.apply(lambda col: pd.to_numeric(col, errors='coerce')).fillna(0)
        wiki_movies_df['running_time'] = running_time_extract.apply(lambda row: row[0]*60 + row[1] if row[2] == 0 else row[2], axis=1)

    # Return three variables. The first is the wiki_movies_df DataFrame
        return wiki_movies_df, kaggle_metadata, ratings


In [37]:
# 17. Create the path to your file directory and variables for the three files.
file_dir = 'Data'
# The Wikipedia data
wiki_file = f'{file_dir}/wikipedia-movies.json'
# The Kaggle metadata
kaggle_file = f'{file_dir}/movies_metadata.csv'
# The MovieLens rating data.
ratings_file = f'{file_dir}/ratings.csv'

In [38]:
# 18. Set the three variables equal to the function created in D1.
wiki_file, kaggle_file, ratings_file = extract_transform_load()

TypeError: cannot unpack non-iterable NoneType object

In [ ]:
# 19. Set the wiki_movies_df equal to the wiki_file variable. 
wiki_movies_df = wiki_file

In [ ]:
# 20. Check that the wiki_movies_df DataFrame looks like this. 
wiki_movies_df.head()

In [ ]:
# 21. Check that wiki_movies_df DataFrame columns are correct. 
wiki_movies_df.columns.to_list()